In [28]:
import numpy as np
import random
import matplotlib.pyplot as plt
import matplotlib.lines as mlines

from game import Game
from player import Player

In [29]:
from adam import Adam

In [30]:
### Generate cards from 9 to 14 (ace) for all colors/symbols (0, 1, 2, 3)
def getDeck():
    return [(number, color) for color in range(4) for number in range(9, 15)]
    
print(getDeck())

[(9, 0), (10, 0), (11, 0), (12, 0), (13, 0), (14, 0), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (9, 2), (10, 2), (11, 2), (12, 2), (13, 2), (14, 2), (9, 3), (10, 3), (11, 3), (12, 3), (13, 3), (14, 3)]


In [31]:
### Shuffle the cards randomly. Each player gets 9 cards
### (so one player cannot be certain which cards the other player has)

def getShuffled(deck):
    D = set(deck)
    A = set(random.sample(deck, 8))
    B = set(random.sample(list(D - A), 8))
    C = D - A - B
    if len(A.intersection(B)) > 0: print("Shuffle error 1")
    if len(A.intersection(B)) > 0: print("Shuffle error 2")
    if len(A.intersection(C)) > 0: print("Shuffle error 3") 
    DS = A | B | C
    if not DS == D: print("Shuffle error 4")  
    return list(A), list(B), list(C)

p1, p2, notUsed, = getShuffled(getDeck())
print(p1)
print(p2)


[(9, 0), (13, 1), (14, 1), (13, 0), (9, 2), (14, 0), (13, 2), (10, 2)]
[(11, 1), (9, 3), (12, 0), (11, 3), (12, 3), (13, 3), (11, 2), (14, 3)]


In [32]:
# Some examplary random player

class RandomPlayer(Player):
    
    ### player's random strategy
    def putCard(self, declared_card):
        
        ### check if must draw
        if len(self.cards) == 1 and declared_card is not None and self.cards[0][0] < declared_card[0]:
            return "draw"
        
        ### player randomly decides which card put on the table
        card = random.choice(self.cards)
        declaration = card
        
        ### player randomly decides whether to cheat or not
        cheat = np.random.choice([True, False])
       
        ### if (s)he decides to cheat, (s)he randomly declares the card.
        if cheat:
            declaration = random.choice(self.cards)             
            
        ### Yet, declared card should be no worse than a card on the top of the pile . 
        if declared_card is not None and declaration[0] < declared_card[0]:
            declaration = (min(declared_card[0]+1,14), declaration[1])

        ### return the decision (true card) and declaration (player's declaration)
        return card, declaration
    
    ### randomly decides whether to check or not
    def checkCard(self, opponent_declaration):
        return np.random.choice([True, False])
    

Analyze few moves...

In [33]:
### Perform a full game 100 times
STAT_NAMES = ["Wins", "Draws", "Moves", "Cards", "Pile Size", "Checks", "Draw Decisions", "Cheats", "Errors", "Total errors"]
ANALYZE_STATS = [0, 1, 2, 3, 5, 6, 7, 8]

def printResults(results):
    print("Wins:")
    print(results[0])
    print("Draws:")
    print(results[1])
    print("Moves:")
    print(stats_moves[2])
    print("Cards:")
    print(results[3])
    print("Pile size:")
    print(results[4])
    print("Checks:")
    print(results[5])
    print("Draw decisions:")
    print(results[6])
    print("Cheats:")
    print(results[7])
    print("Errors:")
    print(results[8])
    print("Total errors:")
    print(results[9])

def comparePlayers(player1, player2, repeats=10, log_turn=False):
    stats_wins = [0, 0]
    stats_draws = [0, 0]
    stats_moves = [0, 0]
    stats_cards = [0, 0]
    stats_pile_size = 0
    stats_checks = [0, 0]
    stats_draw_decisions = [0, 0]
    stats_cheats = [0, 0]
    stats_errors = [0, 0]
    
    errors = 0
    draws = 0

    for t in range(repeats):
        game = Game([player1, player2], log = False)
    
        error = False
        draw = False
        
        while True:
            valid, player = game.takeTurn(log = log_turn)
            print("Game moves: ", game.moves)
            if game.moves[0] > 100 or game.moves[1] > 100:
                draws += 1
                stats_draws[0] += 1
                stats_draws[1] += 1
                if (game.player_cards[0] < game.player_cards[1]):
                    stats_wins[0] += 1
                if (game.player_cards[0] > game.player_cards[1]):
                    stats_wins[1] += 1
                    
                    
                draw=True
                print("DRAW")
                break
            if not valid:
                error = True
                stats_errors[player] += 1
                errors += 1
                break
            if game.isFinished(log = False):
                stats_wins[player] += 1
                break
            
        stats_pile_size += len(game.pile)
        if error: continue
        #if draw: continue
       
        for j in range(2):
            stats_moves[j] += game.moves[j]
            stats_cheats[j] += game.cheats[j]
            stats_checks[j] += game.checks[j]
            stats_draw_decisions[j] += game.draw_decisions[j]
            stats_cards[j] += len(game.player_cards[j])

    div = repeats - errors
    if div > 0:
            
        stats_pile_size /= div          
        for j in range(2):
            stats_moves[j] /= div
            stats_cheats[j] /= div
            stats_checks[j] /= div
            stats_draw_decisions[j] /= div
            stats_cards[j] /= div
            
    return [stats_wins, stats_draws, stats_moves, stats_cards, stats_pile_size, stats_checks, 
            stats_draw_decisions, stats_cheats, stats_errors, errors, draws]  


# COMPARE

In [34]:
from players import AccountantFactory, Acer, Saint, CheatySaint

acc_min = AccountantFactory(min_cheat=True, log=False)
acc_max = AccountantFactory(min_cheat=False, log=False)

strategy = [
    ["RandomPlayer", "RANDOM", RandomPlayer],
    ["Saint", "Saint", Saint],
    ["CheatySaint", "CheatySaint", CheatySaint],
    ["AcePlayer", "Acer", Acer],
    ["SaintyAccountant", "SaintyAccountant", acc_min],
    ["CheatyAccountant", "CheatyAccountant", acc_max],
]

In [35]:
full_results = [[None for i in range(len(strategy))] for i in range(len(strategy))]

for A in range(len(strategy)):
    print("==== " + str(A), strategy[A][0])
    for B in range(A + 1, len(strategy)):
        print(B, strategy[B][0])
        player1 = strategy[A][2](strategy[A][1])
        player2 = strategy[B][2](strategy[B][1])
        results = comparePlayers(player1, player2, 500, False)
        full_results[A][B] = results

==== 0 RandomPlayer
1 Saint
Game moves:  [0, 1]
Game moves:  [1, 1]
Game moves:  [1, 2]
Game moves:  [2, 2]
Game moves:  [2, 3]
Game moves:  [3, 3]
Game moves:  [3, 4]
Game moves:  [4, 4]
Game moves:  [4, 5]
Game moves:  [5, 5]
Game moves:  [5, 6]
Game moves:  [6, 6]
Game moves:  [6, 7]
Game moves:  [7, 7]
Game moves:  [7, 8]
Game moves:  [8, 8]
Game moves:  [8, 9]
Game moves:  [9, 9]
Game moves:  [9, 10]
Game moves:  [10, 10]
Game moves:  [10, 11]
Game moves:  [11, 11]
Game moves:  [11, 12]
Game moves:  [12, 12]
Game moves:  [12, 13]
Game moves:  [13, 13]
Game moves:  [13, 14]
Game moves:  [14, 14]
Game moves:  [14, 15]
Game moves:  [15, 15]
Game moves:  [15, 16]
Game moves:  [1, 0]
Game moves:  [1, 1]
Game moves:  [2, 1]
Game moves:  [2, 2]
Game moves:  [3, 2]
Game moves:  [3, 3]
Game moves:  [4, 3]
Game moves:  [4, 4]
Game moves:  [5, 4]
Game moves:  [5, 5]
Game moves:  [6, 5]
Game moves:  [6, 6]
Game moves:  [7, 6]
Game moves:  [7, 7]
Game moves:  [8, 7]
Game moves:  [8, 8]
Game mo

Simple stats

In [36]:
import pandas as pd


def printMatrix(full_results, stat):
    cur_stat = STAT_NAMES[stat]
    header = [" "] + [S[1] for S in strategy]

    print(cur_stat)
    S = "  \t"
    rows = []
    for s in strategy:
        S += str(s[1]) + " "
    for A in range(len(strategy)):
        row = [str(strategy[A][1])]
        for B in range(len(strategy)):
            if A == B:
                row.append("-")
            elif A < B:
                row.append(full_results[A][B][stat][0])
            else:
                row.append(full_results[B][A][stat][1])
        rows.append(row)
    display(pd.DataFrame(rows, columns=header))
    print()
    print()


for a in ANALYZE_STATS:
    printMatrix(full_results, a)

Wins


RANDOM Saint CheatySaint Acer SaintyAccountant  \
0            RANDOM      -   350         291  365               46   
1             Saint    150     -          77    0              115   
2       CheatySaint    209   423           -   38              151   
3              Acer    135   500         462    -              318   
4  SaintyAccountant    454   385         349  182                -   
5  CheatyAccountant    473   367         318  273              279   

  CheatyAccountant  
0               27  
1              133  
2              182  
3              227  
4              221  
5                -



Draws


RANDOM Saint CheatySaint Acer SaintyAccountant  \
0            RANDOM      -    29           1    9                4   
1             Saint     29     -           0    0                0   
2       CheatySaint      1     0           -    0                0   
3              Acer      9     0           0    -                8   
4  SaintyAccountant      4     0           0    8                -   
5  CheatyAccountant      0     0           0    5                0   

  CheatyAccountant  
0                0  
1                0  
2                0  
3                5  
4                0  
5                -



Moves


...

RANDOM  Saint CheatySaint   Acer SaintyAccountant  \
0            RANDOM       -  0.276       0.346  0.558            0.062   
1             Saint  12.372      -       1.902  4.428            2.774   
2       CheatySaint     1.4  0.734           -   0.14            0.266   
3              Acer     0.0   0.07        0.07      -            0.004   
4  SaintyAccountant    1.27  0.428        0.36    0.4                -   
5  CheatyAccountant   1.128  0.358       0.324  0.762            0.168   

  CheatyAccountant  
0            0.044  
1            2.514  
2            0.258  
3              0.0  
4            0.182  
5                -



Cheats


RANDOM   Saint CheatySaint    Acer SaintyAccountant  \
0            RANDOM       -  19.856       12.87   15.92           12.146   
1             Saint     0.0       -         0.0     0.0              0.0   
2       CheatySaint   8.682   1.688           -   5.228             2.61   
3              Acer  24.252   7.032       6.884       -           20.754   
4  SaintyAccountant   5.846   0.978       1.134  11.106                -   
5  CheatyAccountant   5.282   1.008       0.904   9.846             1.44   

  CheatyAccountant  
0           11.664  
1              0.0  
2            2.346  
3           18.022  
4             1.43  
5                -



Errors


RANDOM Saint CheatySaint Acer SaintyAccountant  \
0            RANDOM      -     0           0    0                0   
1             Saint      0     -           0    0                0   
2       CheatySaint      0     0           -    0                0   
3              Acer      0     0           0    -                0   
4  SaintyAccountant      0     0           0    0                -   
5  CheatyAccountant      0     0           0    0                0   

  CheatyAccountant  
0                0  
1                0  
2                0  
3                0  
4                0  
5                -